In [34]:
import spacy
import pandas as pd
from __future__ import unicode_literals, print_function
import plac
from random import shuffle
from pathlib import Path
from spacy.util import minibatch, compounding
import os

In [18]:
base_data = pd.read_csv('../datasets/TrainNER.csv', delimiter=';', encoding='cp1252')
print('base_data', base_data.describe(), '\n')
train = base_data[:2000]
print('train', train.describe(), '\n')
validation = base_data[-2000:]
print('validation', validation.describe(), '\n')

n_iter = 100

base_data             Sentence #    Word     POS     Tag
count             9000  196645  196645  196645
unique            9000   15323      41      15
top     Sentence: 1367     the      NN       O
freq                 1    9839   27417  166610 

train           Sentence #  Word   POS   Tag
count             89  2000  2000  2000
unique            89   820    36    11
top     Sentence: 86   the    NN     O
freq               1    92   259  1734 

validation             Sentence #  Word   POS   Tag
count               84  1999  1999  1999
unique              84   880    36    11
top     Sentence: 8990   the   NNP     O
freq                 1    98   303  1648 



In [46]:
train.loc['entities'] = train.apply(lambda row: {'entities':[(0, len(str(row['Word'])), str(row['Tag']))]}, axis=1)
train['Word'] = train['Word'].apply(str)
subset = train[['Word', 'entities']]
train_tuples = [tuple(x) for x in subset.values]

/Users/krisztian/anaconda3/lib/python3.6/site-packages/pandas/core/indexing.py:194: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self._setitem_with_indexer(indexer, value)
/Users/krisztian/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.
/Users/krisztian/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/in

In [47]:
nlp = spacy.blank('en')
ner = nlp.create_pipe('ner')
nlp.add_pipe(ner, last=True)

for index, row in train.iterrows():
    ner.add_label(str(row['Tag']))
    
other_pipes = [pipe for pipe in nlp.pipe_names if pipe != 'ner']
with nlp.disable_pipes(*other_pipes):
    optimizer = nlp.begin_training()
    for itn in range(n_iter):
        shuffle(train_tuples)
        losses = {}
        
        batches = minibatch(train_tuples, size=compounding(4., 32., 1.001))
        for batch in batches:
            texts, annotations = zip(*batch)
            nlp.update(
                texts,
                annotations,
                drop=0.5,
                sgd=optimizer,
                losses=losses
            )
        print(itn, losses)

{'ner': 31.37741035625818}
{'ner': 20.411958283846708}
{'ner': 17.779632873089533}
{'ner': 14.946427131673223}
{'ner': 12.658031294301642}
{'ner': 11.105649508302784}
{'ner': 9.24291968514317}
{'ner': 9.315484256794802}
{'ner': 7.823134406774926}
{'ner': 7.342468734099841}
{'ner': 6.851116285629839}
{'ner': 7.105856931563633}
{'ner': 7.419335139888314}
{'ner': 6.92517304093664}
{'ner': 6.593522981238929}
{'ner': 6.071309980892086}
{'ner': 7.172725129423687}
{'ner': 5.195899447410054}
{'ner': 6.009048816125068}
{'ner': 5.5641631542624435}
{'ner': 6.69474270100194}
{'ner': 5.700740700847693}
{'ner': 5.1353108080080085}
{'ner': 5.097582313770623}
{'ner': 5.973059715004398}
{'ner': 5.842348904990789}
{'ner': 5.4836601258707764}
{'ner': 4.412983643039989}
{'ner': 6.185272530549362}
{'ner': 5.312566396371054}
{'ner': 5.958299962910408}
{'ner': 3.6670669922041492}
{'ner': 5.629370732030607}
{'ner': 4.707096306258995}
{'ner': 6.003969169043925}
{'ner': 5.911386958085918}
{'ner': 5.141270327534

In [51]:
validation = base_data

In [52]:
print('\tWord\tPredicate\tTarget')
errors = 0
for _, row in validation.iterrows():
    doc = nlp(str(row['Word']))
    print('\t' + str(row['Word']) + '\t' + doc.ents[0].label_ + '\t' + str(row['Tag']))
    if doc.ents[0].label_ != str(row['Tag']):
        errors += 1
print('Accuracy: ' + str(1 - errors/len(validation.index)))

	Word	Predicate	Target
	President	B-per	B-per
	Karzai	I-per	I-per
	thanked	O	O
	his	O	O
	allies	O	O
	for	O	O
	their	O	O
	help	O	O
	in	O	O
	battling	O	O
	terrorism	O	O
	.	O	O
	The	O	O
	commander	O	O
	of	O	O
	NATO	B-org	B-org
	's	O	O
	Afghan	B-gpe	B-gpe
	force	O	O
	,	O	O
	British	B-gpe	B-org
	General	B-org	I-org
	David	B-per	B-per
	Richards	I-per	I-per
	,	O	O
	said	O	O
	the	O	O
	unity	O	O
	of	O	O
	command	O	O
	the	O	O
	transfer	O	O
	brought	O	O
	will	O	O
	enhance	O	O
	the	O	O
	effectiveness	O	O
	of	O	O
	the	O	O
	overall	O	O
	operation	O	O
	.	O	O
	Referring	O	O
	to	O	O
	the	O	O
	fight	O	O
	in	O	O
	southern	B-geo	B-geo
	Afghanistan	B-geo	I-geo
	since	O	O
	NATO	B-org	B-org
	took	O	O
	command	O	O
	there	O	O
	in	O	O
	July	B-time	B-time
	,	O	O
	Richards	I-per	B-per
	said	O	O
	the	O	O
	NATO	B-org	B-org
	force	O	O
	has	O	O
	shown	O	O
	its	O	O
	resolve	O	O
	to	O	O
	meet	O	O
	the	O	O
	challenges	O	O
	of	O	O
	its	O	O
	expanded	O	O
	mission	O	O
	.	O	O
	Richards	I-per	B-per
	was	O	O
	promoted	O	O
	to

	party	O	O
	's	O	O
	total	O	O
	to	O	O
	47	O	O
	seats	O	O
	.	O	O
	In	O	O
	Saturday	B-time	B-time
	's	O	O
	elections	O	O
	,	O	O
	voters	O	O
	will	O	O
	cast	O	O
	ballots	O	O
	in	O	O
	nine	O	O
	provinces	O	O
	where	O	O
	no	O	O
	candidate	O	O
	won	O	O
	a	O	O
	majority	O	O
	in	O	O
	the	O	O
	previous	O	O
	round	O	O
	of	O	O
	voting	O	O
	.	O	O
	The	O	O
	Muslim	B-org	B-org
	Brotherhood	B-org	I-org
	is	O	O
	banned	O	O
	as	O	O
	a	O	O
	political	O	O
	party	O	O
	,	O	O
	but	O	O
	it	O	O
	endorses	O	O
	so-called	O	O
	independent	O	O
	candidates	O	O
	whose	O	O
	allegiance	O	O
	to	O	O
	the	O	O
	party	O	O
	is	O	O
	known	O	O
	to	O	O
	voters	O	O
	.	O	O
	Hardline	O	O
	lawmakers	O	O
	in	O	O
	Pakistan	B-geo	B-geo
	's	O	O
	North	B-geo	B-geo
	West	I-geo	I-geo
	Frontier	I-geo	I-geo
	Province	I-geo	I-geo
	have	O	O
	pushed	O	O
	through	O	O
	a	O	O
	law	O	O
	that	O	O
	aims	O	O
	to	O	O
	ensure	O	O
	"	O	O
	Islamic	O	O
	correctness	O	O
	"	O	O
	in	O	O
	public	O	O
	places	O	O
	and	O	O
	establishes	O	O
	a	O	O
	morality	O	O

	the	O	O
	Asia	B-org	B-org
	Pacific	I-org	I-org
	Economic	I-org	I-org
	Cooperation	I-org	I-org
	Business	I-org	I-org
	Advisory	I-org	I-org
	Council	I-org	I-org
	are	O	O
	holding	O	O
	meetings	O	O
	this	O	O
	week	O	O
	to	O	O
	finalize	O	O
	their	O	O
	annual	O	O
	report	O	O
	for	O	O
	APEC	B-org	B-org
	leaders	O	O
	who	O	O
	will	O	O
	hold	O	O
	a	O	O
	summit	O	O
	on	O	O
	September	B-time	B-time
	8	I-time	I-time
	and	O	O
	9	B-time	B-time
	.	O	O
	VOA	B-org	B-org
	's	O	O
	Nancy-Amelia	B-per	B-per
	Collins	I-per	I-per
	reports	O	O
	from	O	O
	Sydney	B-geo	B-geo
	.	O	O
	Energy	O	O
	,	O	O
	security	O	O
	,	O	O
	climate	O	O
	change	O	O
	,	O	O
	the	O	O
	World	B-org	B-org
	Trade	I-org	I-org
	Organization	I-org	I-org
	's	O	O
	stalled	O	O
	negotiations	O	O
	,	O	O
	and	O	O
	investment	O	O
	are	O	O
	all	O	O
	expected	O	O
	to	O	O
	be	O	O
	among	O	O
	the	O	O
	major	O	O
	topics	O	O
	in	O	O
	the	O	O
	annual	O	O
	report	O	O
	of	O	O
	the	O	O
	APEC	B-org	B-org
	Business	I-org	I-org
	Advisory	I-org	I-org
	Counci

	hospital	O	O
	in	O	O
	southern	B-geo	O
	Mogadishu	B-geo	B-geo
	.	O	O
	Officials	O	O
	say	O	O
	one	O	O
	suspect	O	O
	was	O	O
	arrested	O	O
	.	O	O
	In	O	O
	Rome	I-org	B-geo
	,	O	O
	a	O	O
	Vatican	B-gpe	B-org
	spokesman	O	O
	deplored	O	O
	the	O	O
	attack	O	O
	and	O	O
	said	O	O
	he	O	O
	hoped	O	O
	it	O	O
	was	O	O
	an	O	O
	isolated	O	O
	event	O	O
	,	O	O
	and	O	O
	not	O	O
	irrationality	O	O
	arising	O	O
	from	O	O
	comments	O	O
	made	O	O
	by	O	O
	the	O	O
	Pope	B-geo	O
	which	O	O
	angered	O	O
	some	O	O
	Muslims	I-per	O
	.	O	O
	Authorities	B-geo	O
	in	O	O
	Mogadishu	B-geo	B-geo
	have	O	O
	not	O	O
	determined	O	O
	a	O	O
	motive	O	O
	for	O	O
	the	O	O
	shooting	O	O
	.	O	O
	The	O	O
	pope	O	O
	has	O	O
	said	O	O
	he	O	O
	meant	O	O
	no	O	O
	offense	O	O
	to	O	O
	Muslims	I-per	O
	when	O	O
	he	O	O
	quoted	O	O
	a	O	O
	14	O	O
	century	O	O
	Byzantine	B-geo	B-per
	emperor	O	O
	as	O	O
	saying	O	O
	some	O	O
	teachings	O	O
	of	O	O
	the	O	O
	Prophet	B-per	B-per
	Muhammed	I-per	I-per
	brought	O	O
	evil	O	O
	to	O

	Union	I-org	I-org
	has	O	O
	deployed	O	O
	troops	O	O
	to	O	O
	Somalia	B-geo	B-geo
	to	O	O
	replace	O	O
	the	O	O
	Ethiopian	B-gpe	B-gpe
	forces	O	O
	,	O	O
	which	O	O
	Addis	B-geo	B-gpe
	Ababa	B-geo	I-gpe
	plans	O	O
	to	O	O
	withdraw	O	O
	.	O	O
	Top	O	O
	Palestinian	B-gpe	B-gpe
	negotiator	O	O
	Ahmed	B-geo	B-per
	Qureia	I-org	I-per
	says	O	O
	Israeli	B-geo	B-gpe
	and	O	O
	Palestinian	B-gpe	B-gpe
	mediators	O	O
	have	O	O
	agreed	O	O
	to	O	O
	prepare	O	O
	a	O	O
	document	O	O
	outlining	O	O
	their	O	O
	progress	O	O
	toward	O	O
	a	O	O
	peace	O	O
	accord	O	O
	.	O	O
	In	O	O
	remarks	O	O
	to	O	O
	reporters	O	O
	,	O	O
	Qureia	I-org	B-per
	said	O	O
	the	O	O
	two	O	O
	sides	O	O
	agreed	O	O
	during	O	O
	recent	O	O
	meetings	O	O
	to	O	O
	begin	O	O
	writing	O	O
	out	O	O
	their	O	O
	positions	O	O
	on	O	O
	all	O	O
	issues	O	O
	discussed	O	O
	during	O	O
	peace	O	O
	negotiations	O	O
	.	O	O
	He	O	O
	did	O	O
	not	O	O
	elaborate	O	O
	on	O	O
	why	O	O
	negotiators	O	O
	had	O	O
	come	O	O
	to	O	O
	the	O	O
	dec

...

	tons	O	O
	of	O	O
	rice	O	O
	is	O	O
	to	O	O
	arrive	O	O
	in	O	O
	the	O	B-geo
	North	B-geo	I-geo
	at	O	O
	the	O	O
	eastern	O	O
	port	O	O
	of	O	O
	Nampo	B-gpe	B-geo
	-	B-per	O
	the	O	O
	first	O	O
	batch	O	O
	of	O	O
	4,00,000	O	O
	tons	O	O
	promised	O	O
	by	O	O
	South	B-geo	B-geo
	Korea	I-gpe	I-geo
	.	O	O
	Seoul	B-geo	B-per
	suspended	O	O
	its	O	O
	regular	O	O
	rice	O	O
	aid	O	O
	after	O	O
	North	B-geo	B-geo
	Korea	I-gpe	I-geo
	conducted	O	O
	missile	O	O
	tests	O	O
	last	O	O
	July	B-time	B-time
	.	O	O
	A	O	O
	nuclear	O	O
	test	O	O
	followed	O	O
	in	O	O
	October	B-time	B-time
	.	O	O
	South	B-geo	B-geo
	Korea	I-gpe	I-geo
	resumed	O	O
	shipments	O	O
	of	O	O
	fertilizer	O	O
	and	O	O
	other	O	O
	emergency	O	O
	aid	O	O
	to	O	O
	the	O	B-geo
	North	B-geo	I-geo
	in	O	O
	late	O	O
	March	I-org	B-time
	,	O	O
	but	O	O
	decided	O	O
	to	O	O
	withhold	O	O
	rice	O	O
	aid	O	O
	until	O	O
	Pyongyang	B-geo	B-geo
	began	O	O
	to	O	O
	carry	O	O
	out	O	O
	its	O	O
	February	I-geo	B-time
	pledge	O	O
	to	O	O
	shut	O

	news	O	O
	agency	O	O
	Xinhua	B-geo	B-org
	reports	O	O
	that	O	O
	one	O	O
	of	O	O
	the	O	O
	new	O	O
	cases	O	O
	came	O	O
	from	O	O
	Guangdong	B-org	B-geo
	province	O	O
	near	O	O
	Hong	B-org	B-geo
	Kong	I-per	I-geo
	.	O	O
	That	B-per	O
	would	O	O
	be	O	O
	the	O	O
	first	O	O
	case	O	O
	outside	O	O
	Sichuan	B-geo	B-geo
	province	O	O
	,	O	O
	where	O	O
	the	O	O
	outbreak	O	O
	began	O	O
	.	O	O
	Xinhua	B-geo	B-org
	says	O	O
	a	O	O
	slaughterhouse	O	O
	worker	O	O
	in	O	O
	Guangdong	B-org	B-geo
	was	O	O
	treated	O	O
	and	O	O
	released	O	O
	from	O	O
	the	O	O
	hospital	O	O
	.	O	O
	Those	B-time	O
	infected	O	O
	have	O	O
	handled	O	O
	infected	O	O
	pigs	O	O
	or	O	O
	infected	O	O
	pork	O	O
	.	O	O
	China	I-org	B-geo
	says	O	O
	there	O	O
	has	O	O
	been	O	O
	no	O	O
	human-to-human	O	O
	transmission	O	O
	of	O	O
	the	O	O
	disease	O	O
	.	O	O
	Police	O	O
	in	O	O
	Nepal	B-gpe	B-gpe
	have	O	O
	arrested	O	O
	at	O	O
	least	O	O
	120	O	O
	anti-government	O	O
	activists	O	O
	across	O	O
	the	O	O
	country	O	O
	who	

	Catholic	B-gpe	I-org
	leader	O	O
	,	O	O
	while	O	O
	saying	O	O
	the	O	O
	next	O	O
	pope	O	O
	should	O	O
	come	O	O
	from	O	O
	Africa	B-geo	B-geo
	.	O	O
	The	O	O
	South	B-geo	B-org
	African	B-org	I-org
	Nobel	B-gpe	I-org
	Peace	B-geo	I-org
	Prize	B-geo	I-org
	winner	O	O
	said	O	O
	Sunday	B-time	B-time
	he	O	O
	hopes	O	O
	cardinals	O	O
	will	O	O
	elect	O	O
	an	O	O
	African	B-org	B-gpe
	when	O	O
	they	O	O
	meet	O	O
	this	O	O
	month	O	O
	at	O	O
	the	O	O
	Vatican	B-gpe	B-geo
	.	O	O
	Also	B-org	O
	today	B-time	B-time
	,	O	O
	the	O	O
	head	O	O
	of	O	O
	Ethiopia	I-per	B-geo
	's	O	O
	Orthodox	I-per	B-geo
	church	O	O
	,	O	O
	Abune	B-geo	B-per
	Paulos	B-geo	I-per
	,	O	O
	praised	O	O
	John	B-org	B-per
	Paul	B-geo	I-per
	as	O	O
	a	O	O
	great	O	O
	man	O	O
	who	O	O
	spoke	O	O
	of	O	O
	peace	O	O
	among	O	O
	religions	O	O
	.	O	O
	Nigeria	B-geo	B-geo
	's	O	O
	President	B-per	B-per
	Olusegun	B-time	I-per
	Obasanjo	B-time	I-per
	expressed	O	O
	his	O	O
	condolences	O	O
	,	O	O
	noting	O	O
	the	O	O
	late	O	O

	international	O	O
	incentives	O	O
	package	O	O
	Tehran	B-gpe	B-geo
	would	O	O
	get	O	O
	by	O	O
	suspending	O	O
	enrichment	O	O
	activities	O	O
	.	O	O
	Iranian	B-gpe	B-gpe
	President	B-per	B-per
	Mahmoud	B-gpe	I-per
	Ahmadinejad	B-geo	I-per
	said	O	O
	Thursday	B-time	B-time
	Iran	B-gpe	B-geo
	is	O	O
	still	O	O
	considering	O	O
	the	O	O
	incentives	O	O
	package	O	O
	.	O	O
	The	O	O
	United	B-gpe	B-geo
	States	I-gpe	I-geo
	and	O	O
	its	O	O
	Western	I-geo	B-per
	allies	O	O
	believe	O	O
	Iran	B-gpe	B-geo
	is	O	O
	trying	O	O
	to	O	O
	develop	O	O
	nuclear	O	O
	weapons	O	O
	.	O	O
	Tehran	B-gpe	B-geo
	says	O	O
	its	O	O
	nuclear	O	O
	program	O	O
	is	O	O
	only	O	O
	for	O	O
	peaceful	O	O
	purposes	O	O
	.	O	O
	Indian	B-gpe	B-gpe
	Prime	O	B-per
	Minister	I-per	O
	Manmohan	I-per	B-per
	Singh	B-geo	I-per
	begins	O	O
	a	O	O
	two-day	O	B-time
	visit	O	O
	to	O	O
	Afghanistan	B-geo	B-geo
	on	O	O
	Sunday	B-time	B-time
	,	O	O
	the	O	O
	first	O	O
	by	O	O
	an	O	O
	Indian	B-gpe	B-gpe
	premier	O	O
	in	O	O
	near

	statement	O	O
	said	O	O
	the	O	O
	U.S.	B-gpe	B-geo
	coordinated	O	O
	with	O	O
	the	O	O
	two	O	O
	countries	O	O
	'	O	O
	governments	O	O
	to	O	O
	ensure	O	O
	a	O	O
	secure	O	O
	transfer	O	O
	.	O	O
	The	O	O
	Guantanamo	B-org	B-geo
	prison	O	O
	houses	O	O
	alleged	O	O
	terrorists	O	O
	,	O	O
	many	O	O
	held	O	O
	for	O	O
	years	O	O
	without	O	O
	trial	O	O
	.	O	O
	The	O	O
	facility	O	O
	has	O	O
	been	O	O
	widely	O	O
	criticized	O	O
	by	O	O
	human	O	O
	rights	O	O
	groups	O	O
	.	O	O
	President	B-per	B-per
	Barack	B-geo	I-per
	Obama	B-time	I-per
	ordered	O	O
	the	O	O
	facility	O	O
	to	O	O
	be	O	O
	shut	O	O
	down	O	O
	within	O	O
	a	O	O
	year	O	O
	after	O	O
	he	O	O
	took	O	O
	office	O	O
	in	O	O
	January	B-time	B-time
	2009	O	I-time
	.	O	O
	However	B-org	O
	,	O	O
	the	O	O
	deadline	O	O
	passed	O	O
	amid	O	O
	difficulty	O	O
	in	O	O
	finding	O	O
	places	O	O
	to	O	O
	put	O	O
	the	O	O
	detainees	O	O
	.	O	O
	More	I-org	O
	than	O	O
	40	O	O
	other	O	O
	countries	O	O
	have	O	O
	accepted	O	O
	at	O	O
	least